In [12]:
import gymnasium as gym
from pogema import GridConfig
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline

grid_config = GridConfig(
    size=16,
    density=0.5,
    num_agents=1,
    max_episode_steps=64
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:29: UserWarning: WARN: It seems a Box observation space is an image but the `dtype` is not `np.uint8`, actual type: float32. If the Box observation space is not an image, we recommend flattening the observation to have only a 1D vector.
  logger.warn(
/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:34: UserWarning: WARN: It seems a Box observation space is an image but the lower and upper bounds are not [0, 255]. Actual lower bound: -1.0, upper bound: 1.0. Generally, CNN policies assume observations are within that range, so you may encounter an issue if the observation values are not.
  logger.warn(


#### Optuna Integration

In [13]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(5.0e5)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4, timeout=600)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


[I 2023-11-10 16:32:26,331] A new study created in memory with name: no-name-dd8452fc-2d9a-4acd-98a7-05526eb83ac5
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 77        |
|    ep_rew_mean        | 0.333     |
| time/                 |           |
|    fps                | 233       |
|    iterations         | 100       |
|    time_elapsed       | 2         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -6.97e-08 |
|    explained_variance | 0.0151    |
|    learning_rate      | 0.056     |
|    n_updates          | 99        |
|    policy_loss        | -0        |
|    value_loss         | 0.012     |
----------------

[I 2023-11-10 17:19:43,726] Trial 2 finished with value: 1.0 and parameters: {'gamma': 0.03764379891594956, 'lr': 0.00010326521385250612}. Best is trial 2 with value: 1.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 40.8      |
|    ep_rew_mean        | 0.5       |
| time/                 |           |
|    fps                | 167       |
|    iterations         | 95300     |
|    time_elapsed       | 2838      |
|    total_timesteps    | 476500    |
| train/                |           |
|    entropy_loss       | -7.38e-08 |
|    explained_variance | -0.703    |
|    learning_rate      | 0.056     |
|    n_updates          | 95299     |
|    policy_loss        | -0        |
|    value_loss         | 0.00384   |
-------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 39.1     |
|    ep_rew_mean        | 0.54     |
| time/                 |          |
|    fps                | 166      |
|    iterations         | 94700    |
|    time_elapsed       | 2838     |
|    total_timesteps    | 473500   |
| train/             

[I 2023-11-10 17:21:11,297] Trial 3 finished with value: 0.0 and parameters: {'gamma': 0.01555985420195519, 'lr': 0.05595482406570459}. Best is trial 2 with value: 1.0.


------------------------------------
| rollout/              |          |
|    ep_len_mean        | 36.7     |
|    ep_rew_mean        | 0.48     |
| time/                 |          |
|    fps                | 169      |
|    iterations         | 99300    |
|    time_elapsed       | 2925     |
|    total_timesteps    | 496500   |
| train/                |          |
|    entropy_loss       | -1.22    |
|    explained_variance | -11.7    |
|    learning_rate      | 2.98e-05 |
|    n_updates          | 99299    |
|    policy_loss        | -0.0154  |
|    value_loss         | 0.000264 |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 23.6     |
|    ep_rew_mean        | 0.73     |
| time/                 |          |
|    fps                | 164      |
|    iterations         | 96200    |
|    time_elapsed       | 2925     |
|    total_timesteps    | 481000   |
| train/                |          |
|

[I 2023-11-10 17:21:18,411] Trial 0 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.017675360622156584, 'lr': 2.984311086096306e-05}. Best is trial 2 with value: 1.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 20.7      |
|    ep_rew_mean        | 0.77      |
| time/                 |           |
|    fps                | 165       |
|    iterations         | 96900     |
|    time_elapsed       | 2932      |
|    total_timesteps    | 484500    |
| train/                |           |
|    entropy_loss       | -0.0424   |
|    explained_variance | 1.79e-07  |
|    learning_rate      | 0.00038   |
|    n_updates          | 96899     |
|    policy_loss        | -1.12e-05 |
|    value_loss         | 3.93e-06  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 22.9      |
|    ep_rew_mean        | 0.73      |
| time/                 |           |
|    fps                | 165       |
|    iterations         | 97000     |
|    time_elapsed       | 2932      |
|    total_timesteps    | 485000    |
| train/    

[I 2023-11-10 17:21:28,911] Trial 1 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.00592817520938753, 'lr': 0.00038004764986176905}. Best is trial 2 with value: 1.0.


Number of finished trials:  4
Best trial:
  Value:  1.0
  Params: 
    gamma: 0.03764379891594956
    lr: 0.00010326521385250612
  User attrs:
    gamma: 0.9623562010840504


### Train agent with best hyper parameters

In [14]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.03764379891594956,#0.005090895994889371,
    learning_rate=0.00010326521385250612#0.03807432884729837,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [15]:
# Train agent and save it
a2c_model.learn(int(5.0e5))
a2c_model.save("saved/a2c_b")

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 38.4     |
|    ep_rew_mean        | 0.615    |
| time/                 |          |
|    fps                | 1397     |
|    iterations         | 100      |
|    time_elapsed       | 0        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.61    |
|    explained_variance | -8.9     |
|    learning_rate      | 0.000103 |
|    n_updates          | 99       |
|    policy_loss        | -0.0644  |
|    value_loss         | 0.00216  |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 33.2     |
|    ep_rew_mean        | 0.655    |
| time/                 |          |
|    fps                | 1420     |
|    iterations         | 200      |
|    time_elapsed       | 0        |
|    total_timesteps    | 1000     |
| train/                |          |
|

#### Testing 

In [16]:
a2c_model = A2C.load("saved/a2c_b")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:0.75 +/- 0.43


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


In [20]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=1000):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 64
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"media_b/render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
3 64 0 False
4 63 0 False
3 62 0 False
3 61 0 False
3 60 0 False
2 59 0 False
3 58 0 False
3 57 0 False
2 56 0 False
2 55 0 False
2 54 0 False
2 53 0 False
2 52 0 False
4 51 0 True
---1---
2 64 1 False
3 63 1 True
---2---
4 64 2 True
---3---
4 64 3 False
1 63 3 True
---4---
1 64 4 False
1 63 4 True
---5---
1 64 5 False
1 63 5 False
2 62 5 False
1 61 5 False
3 60 5 False
3 59 5 False
3 58 5 False
1 57 5 True
---6---
2 64 6 True
---7---
1 64 7 False
4 63 7 True
---8---
3 64 8 False
3 63 8 False
1 62 8 True
---9---
1 64 9 False
1 63 9 False
3 62 9 True
---10---
4 64 10 False
2 63 10 False
2 62 10 False
2 61 10 False
2 60 10 False
2 59 10 False
2 58 10 False
2 57 10 False
2 56 10 False
2 55 10 False
2 54 10 False
1 53 10 False
2 52 10 False
2 51 10 False
2 50 10 False
2 49 10 False
2 48 10 False
2 47 10 False
2 46 10 False
2 45 10 False
2 44 10 False
2 43 10 False
2 42 10 False
2 41 10 False
2 40 10 False
2 39 10 False
2 38 10 False
2 37 10 False
2 36 10 False
2 35 10 False
4 34 10

In [21]:
step_array

[14,
 2,
 1,
 2,
 2,
 8,
 1,
 2,
 3,
 3,
 34,
 3,
 3,
 20,
 2,
 1,
 4,
 3,
 12,
 1,
 4,
 12,
 5,
 4,
 3,
 1,
 5,
 6,
 1,
 4,
 2,
 1,
 2,
 2,
 1,
 4,
 5,
 8,
 2,
 7,
 7,
 2,
 2,
 1,
 3,
 7,
 7,
 2,
 5,
 7,
 6,
 3,
 5,
 21,
 3,
 2,
 4,
 1,
 4,
 2,
 1,
 49,
 11,
 1,
 2,
 1,
 2,
 19,
 4,
 3,
 1,
 1,
 5,
 5,
 8,
 10,
 3,
 2,
 2,
 17,
 4,
 1,
 7,
 4,
 9,
 1,
 2,
 3,
 4,
 4,
 2,
 2,
 6,
 16,
 2,
 4,
 12,
 2,
 7,
 9,
 12,
 1,
 1,
 6,
 1,
 1,
 11,
 4,
 1,
 3,
 26,
 6,
 10,
 9,
 11,
 3,
 49,
 5,
 1,
 2,
 2,
 3,
 5,
 2,
 3,
 3,
 4,
 13,
 2,
 5,
 3,
 5,
 11,
 1,
 1,
 3,
 5,
 2,
 2,
 4,
 33,
 2,
 1,
 3,
 4,
 4,
 1,
 1,
 2,
 9,
 6,
 3,
 4,
 7,
 1,
 2,
 4,
 9,
 5,
 1,
 32,
 2,
 42,
 1,
 6,
 1,
 5,
 3,
 3,
 2,
 9,
 4,
 2,
 1,
 1,
 1,
 50,
 4,
 6,
 1,
 10,
 3,
 3,
 1,
 2,
 4,
 6,
 13,
 2,
 32,
 4,
 4,
 3,
 1,
 5,
 7,
 5,
 4,
 5,
 1,
 4,
 6,
 6,
 7,
 27,
 3,
 6,
 14,
 2,
 1,
 1,
 5,
 10,
 8,
 1,
 2,
 2,
 18,
 3,
 3,
 2,
 3,
 25,
 10,
 46,
 2,
 3,
 3,
 2,
 1,
 2,
 1,
 18,
 5,
 7,
 7,
 4,
 2,
 3,
 2,
 2,


In [22]:
import numpy as np
np.mean(step_array)

5.966857142857143

In [23]:
from IPython.display import SVG, display
from utils.util import *

MODEL_NAME = f"saved/a2c_b"
MAX_EPISODE_STEPS = 64
MAX_TRIALS = 1000
SAVE_METRICS_PATH = 'saved/evaluation_metrics.yml'


metrics = evaluate_metrics(a2c_model, env, MODEL_NAME, num_episodes=MAX_EPISODE_STEPS, num_trials=MAX_TRIALS, verbose=False, save_animation=False)
save_metrics(metrics, MODEL_NAME, SAVE_METRICS_PATH)
print(f"Agent Success Rate: {metrics['success_rate'] * 100:.2f}%")
print(f"Steps to termination : {metrics['step_array']}")
print(f"Average steps to termination : {metrics['ave_steps']}")

Agent Success Rate: 87.50%
Steps to termination : [1, 2, 3, 8, 8, 1, 1, 4, 13, 4, 1, 2, 2, 14, 23, 2, 1, 27, 35, 7, 43, 3, 41, 1, 1, 1, 2, 2, 7, 4, 1, 1, 1, 2, 21, 2, 3, 1, 6, 5, 1, 2, 3, 4, 2, 7, 1, 1, 4, 44, 1, 13, 2, 2, 3, 7, 4, 3, 22, 5, 19, 8, 1, 1, 2, 3, 4, 3, 8, 2, 4, 26, 2, 15, 2, 9, 1, 1, 4, 3, 3, 4, 3, 5, 1, 6, 2, 7, 40, 4, 1, 3, 5, 2, 1, 13, 2, 13, 3, 5, 3, 9, 9, 7, 3, 3, 1, 2, 20, 2, 2, 1, 2, 6, 5, 12, 2, 1, 1, 1, 3, 1, 1, 4, 2, 7, 3, 5, 8, 4, 6, 6, 10, 1, 2, 3, 1, 2, 2, 3, 7, 1, 2, 2, 1, 60, 7, 1, 5, 2, 2, 6, 3, 1, 1, 4, 2, 6, 5, 42, 7, 5, 1, 5, 3, 1, 2, 5, 50, 2, 7, 1, 6, 2, 2, 6, 3, 2, 5, 1, 1, 5, 3, 7, 3, 3, 2, 2, 3, 2, 5, 1, 18, 1, 4, 2, 2, 5, 7, 6, 4, 12, 3, 45, 3, 8, 2, 1, 1, 21, 10, 9, 21, 1, 4, 4, 1, 2, 15, 1, 2, 4, 18, 22, 3, 1, 4, 2, 1, 3, 7, 4, 5, 2, 5, 8, 8, 2, 6, 7, 1, 7, 4, 2, 1, 10, 3, 2, 1, 3, 10, 3, 1, 13, 4, 2, 1, 1, 3, 5, 1, 40, 5, 4, 29, 6, 3, 10, 44, 5, 1, 1, 50, 2, 15, 5, 7, 2, 1, 2, 10, 5, 3, 7, 4, 4, 13, 3, 3, 2, 4, 4, 14, 2, 2, 8, 13, 9, 2, 1, 6, 1